# Geomapping exploration

This notebook is an exploratory look at the methods I can use to overlay activity data from the Strava API onto a basemap

##  Strava API Setup

In [63]:
import json
import requests
import urllib3
import pandas as pd
import polyline
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

class StravaAPI():
    def __init__(self, codes_path):
        with open(codes_path, 'r') as f:
            self.codes = json.load(f) # TODO: NEED TO USE social_django.models.UserSocialAuth to get the Strava login for all users
        
    def get_user_data(self):
        auth_url = "https://www.strava.com/oauth/token"
        user_url = "https://www.strava.com/api/v3/athlete"


        # Get access token
        #         print("Requesting Token...\n")
        res = requests.post(auth_url, data=self.codes, verify=False)
        access_token = res.json()['access_token']
        #         print("Access Token = {}\n".format(access_token))

        # Get activity data
        header = {'Authorization': 'Bearer ' + access_token}
        activity_df_list = []

        x = requests.get(user_url, headers = header).json
        user_json = requests.get(user_url, headers=header).json()
        user_data = pd.json_normalize(user_json)

        return user_data
    
    def get_activities(self):

        auth_url = "https://www.strava.com/oauth/token"
        activites_url = "https://www.strava.com/api/v3/athlete/activities"


        # Get access token
        #         print("Requesting Token...\n")
        res = requests.post(auth_url, data=self.codes, verify=False)
        access_token = res.json()['access_token']
        #         print("Access Token = {}\n".format(access_token))

        # Get activity data
        header = {'Authorization': 'Bearer ' + access_token}
        activity_df_list = []
        for n in range(5):  # TODO: Change this to be higher
            param = {'per_page': 200, 'page': n+1}

            activities_json = requests.get(activites_url, headers=header, params=param).json()
            if not activities_json:
                break
            activity_df_list.append(pd.json_normalize(activities_json))
        activities_df = pd.concat(activity_df_list)
        print('Imported', len(activities_df),'activities')

        return activities_df
    def prep_df(self, activities_df):
            activities_df['polylines'] = activities_df['map.summary_polyline']
            activities_df['activity_id'] = activities_df['id']
            activities_df['user_id'] = activities_df['athlete.id']
            activities_df['start_date_utc'] = activities_df['start_date']
            prepped_activities_df = activities_df[['user_id','activity_id','type', 'start_date_utc','start_date_local','timezone','polylines']]
            prepped_activities_df = prepped_activities_df.dropna(subset = ['polylines'])
            prepped_activities_df['polylines'] = prepped_activities_df['polylines'].apply(polyline.decode)
            prepped_activities_df = prepped_activities_df.reset_index(drop = True)
            prepped_activities_df['start_date_utc'] = pd.to_datetime(prepped_activities_df['start_date_utc'])
            prepped_activities_df['start_date_local'] = pd.to_datetime(prepped_activities_df['start_date_local'])
            return prepped_activities_df
            

In [64]:
s = StravaAPI('codes.json')
activities_df = s.get_activities()
prepped_df = s.prep_df(activities_df)
user_data = s.get_user_data()

Imported 506 activities


In [65]:
user_data

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit            created_at            updated_at  \
0    None   M    False   False  2019-10-21T16:38:28Z  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [55]:
s=StravaAPI('codes.json')
s.get_user_data()['id']

47608726

In [46]:
user_data.to_sql("painting_app_users", engine, if_exists='replace', index=False)

In [20]:
from shapely.geometry import Polygon
import folium

def add_polylines(m, polylines, color, opacity = 0.6):
    feature_group = folium.FeatureGroup()
    for line in polylines:
        folium.PolyLine(locations=line, color=color, opacity = opacity).add_to(feature_group)
    feature_group.add_to(m)
def latlong_to_gridcoords(lat, long, width = 0.001):
    """
    Determines the grid point a latitude and longitude would fall in if each grid space had dimensions lat/width and long/width
    
    For 0.001 that means there will be 360000 longitudes and 180000 latitude grid points over the entirety of the globe
    """
    grid_lat = round((lat + 90)/width)
    grid_long = round((long+180)/width)
    return grid_lat, grid_long
    from django.contrib.gis.geos import Polygon
def gridcoords_to_polygon(grid_lat, grid_long, color = None, width = 0.001,  weight = 0.1, fill_opacity = 0.5, popup = None, package = 'folium'):
    """
    Turns a grid point, as defined in get_gridcoords() into a square polygon with side length = width
    """
    lat_center = grid_lat*width-90
    long_center = grid_long*width-180
    lats = [lat_center-width/2,lat_center-width/2,lat_center+width/2,lat_center+width/2,lat_center-width/2]
    longs = [long_center-width/2,long_center+width/2,long_center+width/2,long_center-width/2,long_center-width/2]
    if package == 'folium':
        polygon = folium.Polygon(list(zip(lats,longs)),color=color, weight=weight, fill=True, fill_color=color, fill_opacity=fill_opacity, popup = popup) 
    if package == 'shapely':
        polygon = Polygon(list(zip(lats,longs)))
    return polygon

In [21]:
import random 

m = folium.Map(tiles='stamentoner', location = [43.45005, -80.42766], zoom_start = 15,prefer_canvas = True) #tiles='OpenStreetMap'
grid_points = {}
a = 0
for i in range(len(prepped_df['polylines'])):
    activity_id = prepped_df['activity_id'].iloc[i]
    user_id = prepped_df['user_id'].iloc[i]
    for j in range(len(prepped_df['polylines'].iloc[i])):
        a+=1
        lat,long = prepped_df['polylines'].iloc[i][j]
        grid_lat, grid_long = latlong_to_gridcoords(lat,long)
        grid_points[str(grid_lat)+"_"+str(grid_long)] = [grid_lat,grid_long]

clrs = ['red','blue','orange']
color_choices = random.choices(clrs, k = len(grid_points.keys()))
feature_group = folium.FeatureGroup()
time = 'Tue Jun  7 17:21:19 2022'
for n,key in enumerate(grid_points.keys()):
    grid_lat,grid_long = grid_points[key]
    x = gridcoords_to_polygon(grid_lat,grid_long, color = color_choices[n], popup = "<b> Time: </b>"+ str(time))
    x.add_to(m)
#     x2 = x.convex_hull
#     color_choice = color_choices[n]
#     folium.GeoJson(x, style_function = lambda a: {'stroke': True, 'color': color_choice, 'weight':0.1, 'fillOpacity':0.5}).add_to(feature_group)
#     if n ==3:
#         break
# feature_group.add_to(m)
# add_polylines(m, prepped_df['polylines'], 'blue')
m
# Next steps are to put this whole system into a nice class and develop a database/storage system to retrieve data


In [5]:
m.save('temp_map.json')

In [10]:
from sqlalchemy import create_engine
import environ
import os

env = environ.Env()
environ.Env.read_env(r'C:\Users\verta\PycharmProjects\paint-the-world\.env')

user = env('USER')
pwd = env('PASSWORD')
host = 'localhost'
port = '5432'
database = 'grid points'
engine = create_engine(f'postgresql+psycopg2://{user}:{pwd}@{host}/{database}')

In [11]:
import time
x = time.time()
user_ids = []
activities_ids = []
lats = []
longs = []
times = []
grid_lats = []
grid_longs = []
width = 0.001

for ind, row in prepped_df.iterrows():
    for lat, long in row['polylines']:
        user_ids.append(row['user_id'])
        activities_ids.append(row['activity_id'])
        lats.append(lat)
        longs.append(long)
        times.append(row['start_date_utc'])

times = pd.to_datetime(times, utc= True)

user_grid_df = pd.DataFrame(
    {'activity_id': activities_ids,'userID': user_ids, 'latitude': lats, 'longitude': longs,
     'time': times})

user_grid_df['grid_lat'] = round((user_grid_df['latitude'] +90)/ width).astype('int64')
user_grid_df['grid_long'] = round((user_grid_df['longitude'] +180)/ width).astype('int64')

full_grid_df = pd.read_sql('SELECT * FROM \"painting_app_allgriddata\"', engine)
full_grid_df['time'] = pd.to_datetime(full_grid_df['time'], utc = True)

new_grid_df = pd.concat([user_grid_df, full_grid_df]).drop_duplicates()


canvas_df = pd.DataFrame(new_grid_df.groupby(['grid_lat','grid_long']).max()).reset_index()
canvas_df = canvas_df[['activity_id', 'userID', 'latitude', 'longitude', 'time', 'grid_lat', 'grid_long']]

new_grid_df.to_sql("painting_app_allgriddata",engine, if_exists = 'replace',index=False)
canvas_df.to_sql("painting_app_canvasgriddata",engine, if_exists = 'replace',index=False)

print(time.time() - x)

3.298997163772583


In [36]:
pd.concat([user_grid_df, full_grid_df]).duplicates

AttributeError: 'DataFrame' object has no attribute 'duplicates'

In [42]:
(~user_grid_df['activity_id'].isin(full_grid_df['activity_id'])).sum()

0

In [12]:
full_grid_df = pd.read_sql('SELECT * FROM \"painting_app_allgriddata\"', engine)
t = full_grid_df['time'][0]

In [13]:
t.strftime("%c")

'Wed Jun  8 21:31:59 2022'

In [33]:
with open(r'C:\Users\verta\PycharmProjects\paint-the-world\templates\maps\full_map.txt','w') as f:
    f.write(m._repr_html_())

In [14]:
import geopandas as gpd

In [15]:
canvas_df = pd.read_sql('SELECT * FROM \"painting_app_canvasgriddata\"', engine)

In [27]:
from shapely.geometry import Polygon
polys = []
for idx, row in canvas_df.iterrows():
    poly = gridcoords_to_polygon(grid_lat,grid_long, package = 'shapely')
    polys.append(poly)
gpd.GeoDataFrame(canvas_df, geometry = gpd.GeoSeries(polys))

activity_id    userID  latitude  longitude                       time  \
0      6501110751  47608726   9.58649  -84.54624  2022-01-05 11:19:37-05:00   
1      6501110751  47608726   9.58663  -84.54591  2022-01-05 11:19:37-05:00   
2      6501110751  47608726   9.58843  -84.54701  2022-01-05 11:19:37-05:00   
3      6501110751  47608726   9.59043  -84.54873  2022-01-05 11:19:37-05:00   
4      6501110751  47608726   9.59117  -84.54922  2022-01-05 11:19:37-05:00   
...           ...       ...       ...        ...                        ...   
3620   5873986850  47608726  50.40237 -122.88354  2021-08-29 14:30:40-04:00   
3621   5873986850  47608726  50.40233 -122.88252  2021-08-29 14:30:40-04:00   
3622   5873986850  47608726  50.40204 -122.88247  2021-08-29 14:30:40-04:00   
3623   5873986850  47608726  50.40272 -122.88553  2021-08-29 14:30:40-04:00   
3624   5873986850  47608726  50.40252 -122.88501  2021-08-29 14:30:40-04:00   

      grid_lat  grid_long                                           geometry  
0        99586      95454  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
1        99587      95454  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
2        99588      95453  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
3        99590      95451  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
4        99591      95451  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
...        ...        ...                                                ...  
3620    140402      57116  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
3621    140402      57117  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
3622    140402      57118  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
3623    140403      57114  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  
3624    140403      57115  POLYGON ((41.47950 -82.68450, 41.47950 -82.683...  

[3625 rows x 8 columns]

In [28]:
gdf = gpd.GeoDataFrame(canvas_df, geometry = gpd.GeoSeries(polys))


In [29]:
gdf.to_sql("painting_app_canvasgriddata",engine, if_exists = 'replace',index=False)

ProgrammingError: (psycopg2.ProgrammingError) can't adapt type 'Polygon'
[SQL: INSERT INTO painting_app_canvasgriddata (activity_id, "userID", latitude, longitude, time, grid_lat, grid_long, geometry) VALUES (%(activity_id)s, %(userID)s, %(latitude)s, %(longitude)s, %(time)s, %(grid_lat)s, %(grid_long)s, %(geometry)s)]
[parameters: ({'activity_id': 6501110751, 'userID': 47608726, 'latitude': 9.58649, 'longitude': -84.54624, 'time': datetime.datetime(2022, 1, 5, 11, 19, 37, tzinfo=datetime.timezone(datetime.timedelta(days=-1, seconds=68400))), 'grid_lat': 99586, 'grid_long': 95454, 'geometry': <shapely.geometry.polygon.Polygon object at 0x000002478C7F8A08>}, {'activity_id': 6501110751, 'userID': 47608726, 'latitude': 9.58663, 'longitude': -84.54591, 'time': datetime.datetime(2022, 1, 5, 11, 19, 37, tzinfo=datetime.timezone(datetime.timedelta(days=-1, seconds=68400))), 'grid_lat': 99587, 'grid_long': 95454, 'geometry': <shapely.geometry.polygon.Polygon object at 0x000002479567FE88>}, {'a

In [84]:
current_users_df = pd.read_sql('SELECT * FROM \"painting_app_users\"', engine)

In [60]:
current_users_df

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit            created_at            updated_at  \
0    None   M    False   False  2019-10-21T16:38:28Z  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [72]:
user_data['created_at'] = 'potato'

In [74]:
pd.concat([user_data, current_users_df]).drop_duplicates()

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit            created_at            updated_at  \
0    None   M    False   False                potato  2019-10-23T14:23:54Z   
0    None   M    False   False  2019-10-21T16:38:28Z  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [76]:
current_users_df

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit            created_at            updated_at  \
0    None   M    False   False  2019-10-21T16:38:28Z  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [78]:

user_data

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit created_at            updated_at  \
0    None   M    False   False     potato  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [83]:
~user_data['id'].isin(current_users_df['id'])[0]

False

In [90]:
47608726 in current_users_df['id']

False

In [100]:
current_users_df

id   username  resource_state firstname lastname   bio  city state  \
0  47608726  adam_vert               2      Adam     Vert  None  None  None   

  country sex  premium  summit            created_at            updated_at  \
0    None   M    False   False  2019-10-21T16:38:28Z  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [103]:
user_data['username'] = 'safsafsa'
user_data

id  username  resource_state firstname lastname   bio  city state  \
0  47608726  safsafsa               2      Adam     Vert  None  None  None   

  country sex  premium  summit created_at            updated_at  \
0    None   M    False   False     potato  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

In [116]:
current_users_df[['id','username','firstname','lastname','sex','city','state','country']].loc[current_users_df['id'] == user_data['id']] = user_data[['id','username','firstname','lastname','sex','city','state','country']]

C:\Users\verta\anaconda3\envs\paint-the-world4\lib\site-packages\pandas\core\indexing.py:1884: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, val, pi)


In [130]:
current_users_df['id'].loc[current_users_df['id'] == user_data['id']][0]

47608726

In [134]:
user_data['color'] = 'BLUE'
user_data = user_data[['id','username','firstname','lastname','sex','city','state','country','color']]
user_data.to_sql("painting_app_users", engine, if_exists='replace', index=False)

In [135]:
user_data

id  username firstname lastname sex  city state country color
0  47608726  safsafsa      Adam     Vert   M  None  None    None  BLUE

id  username  resource_state firstname lastname   bio  city state  \
0  47608726  safsafsa               2      Adam     Vert  None  None  None   

  country sex  premium  summit created_at            updated_at  \
0    None   M    False   False     potato  2019-10-23T14:23:54Z   

   badge_type_id  weight                                     profile_medium  \
0              0     0.0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   

                                             profile friend follower  
0  https://lh3.googleusercontent.com/a/AATXAJz2Bt...   None     None

col1  col2
0     1   abs
1     2  basg
2     3  bfdh

In [128]:
df.loc[df['col1'] == 3,'col2'] = 'potato'
df

col1    col2
0     1     abs
1     2    basg
2     3  potato

In [127]:
np.where([df['col1'] == 3])

(array([0], dtype=int64), array([2], dtype=int64))

In [143]:
current_users_df = pd.read_sql('SELECT * FROM \"painting_app_users\"', engine)

In [144]:
current_users_df

id   username firstname lastname sex  city state country color
0  47608726  adam_vert      Adam     Vert   M  None  None    None  BLUE

In [141]:
current_users_df.loc[current_users_df['id'] == user_df['id'][0],:]

NameError: name 'user_df' is not defined

In [145]:
current_users_df = pd.read_sql('SELECT * FROM \"painting_app_users\"', engine)
canvas_df = pd.read_sql('SELECT * FROM \"painting_app_canvasgriddata\"', engine)

In [147]:
canvas_df

activity_id    userID  latitude  longitude                       time  \
0      6501110751  47608726   9.58649  -84.54624  2022-01-05 11:19:37-05:00   
1      6501110751  47608726   9.58663  -84.54591  2022-01-05 11:19:37-05:00   
2      6501110751  47608726   9.58843  -84.54701  2022-01-05 11:19:37-05:00   
3      6501110751  47608726   9.59043  -84.54873  2022-01-05 11:19:37-05:00   
4      6501110751  47608726   9.59117  -84.54922  2022-01-05 11:19:37-05:00   
...           ...       ...       ...        ...                        ...   
3620   5873986850  47608726  50.40237 -122.88354  2021-08-29 14:30:40-04:00   
3621   5873986850  47608726  50.40233 -122.88252  2021-08-29 14:30:40-04:00   
3622   5873986850  47608726  50.40204 -122.88247  2021-08-29 14:30:40-04:00   
3623   5873986850  47608726  50.40272 -122.88553  2021-08-29 14:30:40-04:00   
3624   5873986850  47608726  50.40252 -122.88501  2021-08-29 14:30:40-04:00   

      grid_lat  grid_long  
0        99586      95454  
1        99587      95454  
2        99588      95453  
3        99590      95451  
4        99591      95451  
...        ...        ...  
3620    140402      57116  
3621    140402      57117  
3622    140402      57118  
3623    140403      57114  
3624    140403      57115  

[3625 rows x 7 columns]

In [152]:
canvas_df_clrs = canvas_df.merge(current_users_df[['id','color']], left_on = 'userID', right_on = 'id')

In [154]:
grid_lats,grid_longs, colors = canvas_df_clrs['grid_lat'],canvas_df_clrs['grid_longs'],canvas_df_clrs['times'],canvas_df_clrs['colors']

In [158]:
grid_lats = canvas_df_clrs['grid_lat']
grid_longs = canvas_df_clrs['grid_long']
colors = canvas_df_clrs['color']
times = canvas_df_clrs['time']

'color'